In [491]:
# first let import the library
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import scipy.stats as stats
import datetime
import plotly.express as px
from IPython.display import display


## Buy and Sell car, discover the vehicle value!

#### At our site, we are dedicated to helping you find and purchase your dream car. Leveraging the power of data science, we offer you valuable insights and a seamless experience to match you with the perfect vehicle. Explore our platform and discover how we can assist you in buying and selling cars with confidence and ease

In [492]:
#path_vehicles = ('C:\\Users\\dejsi\\OneDrive\\Documents\\GitHub\\Project_4.py\\vehicles_us.csv')
#try:
    #vehicles = pd.read_csv(path_vehicles, sep=',')
#except:
    #vehicles = pd.read_csv('/datasets/vehicles_us.csv', sep=',')
#print(vehicles.head())
vehicles = pd.read_csv('C:\\Users\\dejsi\\OneDrive\\Documents\\GitHub\\Project_4.py\\vehicles_us.csv', sep=',')
vehicles.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   price         51525 non-null  int64  
 1   model_year    47906 non-null  float64
 2   model         51525 non-null  object 
 3   condition     51525 non-null  object 
 4   cylinders     46265 non-null  float64
 5   fuel          51525 non-null  object 
 6   odometer      43633 non-null  float64
 7   transmission  51525 non-null  object 
 8   type          51525 non-null  object 
 9   paint_color   42258 non-null  object 
 10  is_4wd        25572 non-null  float64
 11  date_posted   51525 non-null  object 
 12  days_listed   51525 non-null  int64  
dtypes: float64(4), int64(2), object(7)
memory usage: 5.1+ MB


In [493]:
display(vehicles.head(3))
display(vehicles.tail(2))


price  model_year           model condition  cylinders fuel  odometer  \
0   9400      2011.0          bmw x5      good        6.0  gas  145000.0   
1  25500         NaN      ford f-150      good        6.0  gas   88705.0   
2   5500      2013.0  hyundai sonata  like new        4.0  gas  110000.0   

  transmission    type paint_color  is_4wd date_posted  days_listed  
0    automatic     SUV         NaN     1.0  2018-06-23           19  
1    automatic  pickup       white     1.0  2018-10-19           50  
2    automatic   sedan         red     NaN  2019-02-07           79

price  model_year           model condition  cylinders fuel  odometer  \
51523   7455      2013.0  toyota corolla      good        4.0  gas  139573.0   
51524   6300      2014.0   nissan altima      good        4.0  gas       NaN   

      transmission   type paint_color  is_4wd date_posted  days_listed  
51523    automatic  sedan       black     NaN  2018-07-02           71  
51524    automatic  sedan         NaN     NaN  2018-06-05           10

Data processing. 
Check for missing values dublicates, data type and fix them.


In [494]:
#fill the missing values base on grouping, specific columns and calculate mean for model_year, median for odemeter
vehicles['model_year'] = vehicles.groupby('model')['model_year'].transform('median')
vehicles['odometer'] = vehicles.groupby('model')['odometer'].transform('median')


In [495]:
#verify for missing values
print("Missing values in 'model_year':", vehicles['model_year'].isna().sum())

Missing values in 'model_year': 0


In [496]:
print("Missing values in 'odometer':", vehicles['odometer'].isna().sum())

Missing values in 'odometer': 41


In [497]:
# since we have missing values on odometer we can replace the missing values with 0 because we no need to drop the rows.
vehicles['odometer'] = vehicles['odometer'].fillna(0)

In [498]:
# convert the year and odonometer to int
vehicles['model_year'] = vehicles['model_year'].astype(int)
vehicles['odometer'] = vehicles['odometer'].astype(int)
display(vehicles.head(3))
display(vehicles.tail(2))

price  model_year           model condition  cylinders fuel  odometer  \
0   9400        2010          bmw x5      good        6.0  gas    108500   
1  25500        2011      ford f-150      good        6.0  gas    121928   
2   5500        2012  hyundai sonata  like new        4.0  gas    105976   

  transmission    type paint_color  is_4wd date_posted  days_listed  
0    automatic     SUV         NaN     1.0  2018-06-23           19  
1    automatic  pickup       white     1.0  2018-10-19           50  
2    automatic   sedan         red     NaN  2019-02-07           79

price  model_year           model condition  cylinders fuel  odometer  \
51523   7455        2010  toyota corolla      good        4.0  gas    104300   
51524   6300        2013   nissan altima      good        4.0  gas    100319   

      transmission   type paint_color  is_4wd date_posted  days_listed  
51523    automatic  sedan       black     NaN  2018-07-02           71  
51524    automatic  sedan         NaN     NaN  2018-06-05           10

In [499]:
# The index colums it si not necerasy to show up on streamlit, so we can drop this column
vehicles.reset_index(drop=True, inplace=True)

In [500]:
display(vehicles.head(3))

price  model_year           model condition  cylinders fuel  odometer  \
0   9400        2010          bmw x5      good        6.0  gas    108500   
1  25500        2011      ford f-150      good        6.0  gas    121928   
2   5500        2012  hyundai sonata  like new        4.0  gas    105976   

  transmission    type paint_color  is_4wd date_posted  days_listed  
0    automatic     SUV         NaN     1.0  2018-06-23           19  
1    automatic  pickup       white     1.0  2018-10-19           50  
2    automatic   sedan         red     NaN  2019-02-07           79

we drop missing values and we convert column "model_year" from float to integer.

In [501]:
vehicles.duplicated().sum()

0

 we dont have duplicated values.

Nowadays it is important to define what type of fuel car you want to select, so let build a filter and define the verhicles by fules type.

In [502]:
# list the cars by fuel
vehicles_fuel = vehicles['fuel'].unique()
vehicles_fuel


array(['gas', 'diesel', 'other', 'hybrid', 'electric'], dtype=object)

We have 5 type of fuel verhicles: gas, diesel, hybrid, electric, other.

Now that we did create the filter for fuel type, we need to create the slider to define in which range of the year we we are internesting to look the verhicles.


In [503]:
# for the range we need to define the start year and last year by using min an max.
year_min, year_max = int(vehicles['model_year'].min()), int(vehicles['model_year'].max())

In [504]:
#list (range(year_min,year_max))
# work on app.py for creating the range 


## Analyzing the vehicle value

### Let's analyze vehicle prices and determine which characteristics most influence the value. We will examine how different attributes, such as condition, fuel type, model, model year, and odometer, impact the price of vehicles.

In [505]:
# creating the histagram to define verhicles price distrubution
current_year = datetime.datetime.now().year
vehicles['age'] = current_year - vehicles['model_year']
display(vehicles.head(3))

price  model_year           model condition  cylinders fuel  odometer  \
0   9400        2010          bmw x5      good        6.0  gas    108500   
1  25500        2011      ford f-150      good        6.0  gas    121928   
2   5500        2012  hyundai sonata  like new        4.0  gas    105976   

  transmission    type paint_color  is_4wd date_posted  days_listed  age  
0    automatic     SUV         NaN     1.0  2018-06-23           19   14  
1    automatic  pickup       white     1.0  2018-10-19           50   13  
2    automatic   sedan         red     NaN  2019-02-07           79   12

In [506]:
vehicles['price'].max()
vehicles['price'].min()

1

Vehicle price distribution value by condition, fuel, model and year

In [507]:
list_price = ['condition', 'model', 'odometer']

for atribute in list_price:
    fig1 = px.scatter(vehicles, x='price', y='model_year', color=atribute, title='Vehicle price distribution for',
                  labels={'price': 'Vehicles price', 'model_year': 'Vehicle year', atribute: atribute.capitalize()})
    fig1.show()


- the first plot: This plot shows how vehicle prices and model years vary by condition. Higher prices often correspond to newer or better-conditioned vehicles. But we can see that that is not alwys the case. exmple we have vehicles 2011, condition excellent and cost $300K
- second graph Model:- This plot shows the relationship between price and model year, colored by manufacturing year. It highlights how the vehicle's age influences its price.
- third graph odometer: This plot shows the relationship between price and model year, colored by vehicles miles. Its normal to assume that vehicles with 0 miles should cost more than the others, but from the plot we see that vehicle on year 2012 have odometer 105252 mile and cost $375K

In [508]:
# let categoryze the age and see what the correlation with vehicles price, model 

This scatter plot shows the relationship between vehicle price and selected characteristics, with colors indicating different vehicle age categories.

In [509]:
#define category prices and build the plot
def age_category(row):
    if row < 5:
        return '<5'
    elif row >= 5 and row <10:
        return '5-10'
    elif row >= 10 and row <15:
        return '10-15'
    else:
        return 'over 15'

In [510]:
vehicles['age_category'] = vehicles['age'].apply(age_category)
display(vehicles.head(3))

price  model_year           model condition  cylinders fuel  odometer  \
0   9400        2010          bmw x5      good        6.0  gas    108500   
1  25500        2011      ford f-150      good        6.0  gas    121928   
2   5500        2012  hyundai sonata  like new        4.0  gas    105976   

  transmission    type paint_color  is_4wd date_posted  days_listed  age  \
0    automatic     SUV         NaN     1.0  2018-06-23           19   14   
1    automatic  pickup       white     1.0  2018-10-19           50   13   
2    automatic   sedan         red     NaN  2019-02-07           79   12   

  age_category  
0        10-15  
1        10-15  
2        10-15

In [517]:
fig2 = px.scatter(vehicles, x='price', y='model', color='age_category',
                  title='Vehicle age categories for each model vs price',
                  labels={'price': 'Vehicle Price', 'model': 'Vehicle Model', 'age_category': 'Age Category'})

fig2.show()

We can define whisch model of the vehicles fall  on the range 5 - 10 year and compare them with price for each range and model.

Let make anathor analyze what model of the vehicles fall on specific range of prices?

In [512]:
#Let define the prices category and build the plot
def price_category(row):
    if row < 3000:
        return 'price less then $5000'
    elif row >= 5000 and row <20000:
        return 'price between $5000-$20000'
    elif row >= 20000 and row <70000:
        return 'price between $20000-$70000'
    elif row >= 70000 and row <150000:
        return 'price between $70000-$150000'
    else:
        return 'over 150000'

In [532]:
vehicles['price_category'] = vehicles['price'].apply(price_category)

list_agg = vehicles.groupby(['price_category', 'model'])['odometer'].mean().reset_index()

fig3 = px.scatter(list_agg, y='model', x='odometer', color='price_category',
             title='Number of Vehicles by Price Category and Model',
             labels={'model': 'Vehicle Model', 'odometer': 'Vehicles miles', 'price_category': 'Price Categories'})

fig3.show()

From the grafic we can see clear for each model vehicle car and miles fall in specific category price. 

We can see that the car less than $5K fall in range over 80k miles - 140K miles for all the model of the cars.



In [533]:
#display(vehicles.head(3))


#recomandation
we can define the number of cylinders with a high confidence level if we group the data by model and model's year and then take a median number of cylinders

In [515]:
# Visualize the median number of cylinders by model and model year. 
#first let group the parameters and find median.
cylinder = vehicles.groupby(['model', 'model_year'])['odometer'].median().reset_index()
cylinder.rename(columns={'odometer': "median_odemeter"}, inplace=True)


In [516]:
# scater median of cylinder
fig4 = px.scatter(cylinder, x='model_year', y='median_odemeter', color='model', title='Median number of cylinder by model and year',
                  labels={'model_year': 'Vehicles year', 'median_odemeter': 'Median number of cylinder'}, hover_name='Vehicle model')
fig4.show()


The avarage of cylinder for each vehicles model and year are show up on the plot above. Most of the vehicles model fall on avarage 50K-150K cylinder.
